# Global Water Risk Classification

## The Backend

In [1]:
import pandas as pd
import geopandas as gpd

import panel as pn
import param

import holoviews as hv
from holoviews import opts
from holoviews.element import tiles

import geoviews as gv

hv.extension('bokeh', logo=False)
pn.extension()

# App

In [2]:
cols = ['bws_raw','bwd_raw','iav_raw','sev_raw','gtd_raw','rfr_raw','cfr_raw','drr_raw','ucw_raw','udw_raw',
        'usa_raw','mean_infant_mort','mean_light','pop_density', 'label']
data = pd.read_csv("./app_data/dashboard_data_grouped.csv"
                  ).drop('Unnamed: 0', axis=1).rename({'bws_raw': 'Baseline Water Stress',
                            'bwd_raw': 'Baseline Water Withdrawals',
                            'iav_raw': 'Interannual Variation',
                            'sev_raw': 'Seasonal Variation',
                            'gtd_raw': 'Groundwater Table Decline',
                            'rfr_raw': 'Riverine Flood Risk',
                            'cfr_raw': 'Coastal Flood Risk',
                            'drr_raw': 'Drought Risk',
                            'ucw_raw': 'Untreated Connected Wastewater',
                            'udw_raw': 'Unimproved Drinking Water',
                            'usa_raw': 'Unimproved Sanitation',
                            'mean_infant_mort': 'Infant Mortality Rate',
                            'mean_light': 'Nighttime Light',
                            'pop_density': 'Population Density',
                            'label': 'Cluster'}, axis=1)

polys = gpd.read_file('./app_data/clusters.shp')

In [3]:
polys.columns
polys['Cluster'] = polys['Cluster_la'].astype(str)
polys = polys.loc[polys['Cluster'] != '-1']
polys = polys[['Cluster', 'geometry']]

In [4]:
p = hv.Polygons(polys, vdims='Cluster', label='Cluster Map'
               ).opts(tools=['hover'],
                      cmap='Category20b',
                      line_color = 'white',
                      line_width = 0.5,
                      alpha = .8,
                      hover_fill_alpha = 1,
                      height=400, width=800, xaxis=None, yaxis=None)
t = tiles.OSM()
imap = t * p

In [5]:

# Variable Bar Chart
def barChart(var):
    d = data[['Cluster', var]]
#     d = d.loc[d['Cluster'] != -1]
    bar = hv.Bars(d, 'Cluster', var).opts(width=500, height=400, tools=['hover'],
                                          xrotation=90, show_legend=False,
                                          color=hv.dim('Cluster'),
                                          cmap='Category20b',
                                          line_color="white")
    return bar

In [6]:
# dmap = dynClassMap('Cluster')
# clmap = hv.DynamicMap(classMap('./app_data/clusters.png')).opts(width=900, framewise=True)

o = list(data.drop(['Cluster'], axis=1).columns)
variables = pn.widgets.Select(options=o)

@pn.depends(classes=variables.param.value)
def dbar(classes):
    return barChart(classes)

ddbar = hv.DynamicMap(dbar)

panel = pn.Column(
    pn.pane.Markdown('''#Water Risk Map
By Leonardo Hart and John Michael LaSalle'''),
    imap,
    pn.Row(pn.Column(variables,
                     pn.pane.Markdown('''Areas with similar attributes across the different dimensions of water 
                     risk and development are combined into cluster. Each cluster has a unique set of 
                     atributes that can be explored in the on the right. Explore the process behind this 
                     visualization on Github [here](https://github.com/jmlasalle/water-risk-classification) 
                      explore the code behind this visualizatoin in a Jupyter Notebook 
                      [here](https://mybinder.org/v2/gh/jmlasalle/water-risk-classification/master?filepath=app.ipynb)
                      ''')
                    ), ddbar)
)

In [7]:
panel.servable()

Column
    [0] Markdown(str)
    [1] HoloViews(Overlay)
    [2] Row
        [0] Column
            [0] Select(options=['Baseline Water Stress', ...], value='Baseline Water Stress')
            [1] Markdown(str)
        [1] HoloViews(DynamicMap)